# Bokeh Tutorial
## 4 - Final Project
### Cristobal Donoso 
##### may 11, 2019
<font size="1">*This tutorial is based on [the official documentation](https://bokeh.pydata.org/en/latest/docs/user_guide.html
)*</font>

In [1]:
from __future__ import absolute_import, division, print_function, unicode_literals
import tensorflow as tf
from tensorflow.keras import datasets, layers, models
tf.__version__

'1.14.0'

In [2]:
(train_images, train_labels), (test_images, test_labels) = datasets.mnist.load_data()

In [4]:
train_images  = train_images#[0:1000]
train_labels  = train_labels#[0:1000]
test_images  = test_images#[0:500]
test_labels  = test_labels#[0:500]

In [5]:
train_images = train_images.reshape((1000, 28, 28, 1))
test_images = test_images.reshape((500, 28, 28, 1))
train_images, test_images = train_images / 255.0, test_images / 255.0

### Defining the model

In [6]:
model = models.Sequential()
model.add(layers.Conv2D(32, (3, 3), activation='relu', input_shape=(28, 28, 1)))
model.add(layers.MaxPooling2D((2, 2)))
model.add(layers.Conv2D(64, (3, 3), activation='relu'))
model.add(layers.MaxPooling2D((2, 2)))
model.add(layers.Conv2D(64, (3, 3), activation='relu'))
model.add(layers.Flatten())
model.add(layers.Dense(64, activation='relu'))
model.add(layers.Dense(10, activation='softmax'))

W0709 19:17:40.549526 139871838984000 deprecation.py:506] From /opt/anaconda3/envs/tf2/lib/python3.7/site-packages/tensorflow/python/ops/init_ops.py:1251: calling VarianceScaling.__init__ (from tensorflow.python.ops.init_ops) with dtype is deprecated and will be removed in a future version.
Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor


In [7]:
model.summary()


Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
conv2d (Conv2D)              (None, 26, 26, 32)        320       
_________________________________________________________________
max_pooling2d (MaxPooling2D) (None, 13, 13, 32)        0         
_________________________________________________________________
conv2d_1 (Conv2D)            (None, 11, 11, 64)        18496     
_________________________________________________________________
max_pooling2d_1 (MaxPooling2 (None, 5, 5, 64)          0         
_________________________________________________________________
conv2d_2 (Conv2D)            (None, 3, 3, 64)          36928     
_________________________________________________________________
flatten (Flatten)            (None, 576)               0         
_________________________________________________________________
dense (Dense)                (None, 64)                3

In [8]:
model.compile(optimizer='adam',
              loss='sparse_categorical_crossentropy',
              metrics=['accuracy'])

model.fit(train_images, train_labels, epochs=1)

1000/1000 [==============================] - 1s 598us/sample - loss: 1.6495 - acc: 0.5050


In [9]:
y_pred = model.predict_classes(test_images)

### Building an interactive confusion matrix

In [10]:
from bokeh.io import output_notebook, show
output_notebook()

Loading BokehJS ...

In [11]:
from bokeh.models import LinearColorMapper, FixedTicker,TapTool, ColorBar, ColumnDataSource, CustomJS
from bokeh.plotting import figure
from sklearn.metrics import confusion_matrix
import numpy as np

In [12]:
cm = confusion_matrix(test_labels, y_pred)
cm_n = np.round(cm.astype('float') / cm.sum(axis=1)[:, np.newaxis], 2)
cm

array([[42,  0,  0,  0,  0,  0,  0,  0,  0,  0],
       [ 0, 64,  0,  0,  0,  0,  0,  3,  0,  0],
       [ 0,  2, 49,  0,  0,  1,  0,  3,  0,  0],
       [ 0,  2,  6, 27,  0,  3,  0,  6,  1,  0],
       [ 1,  0,  7,  0, 22,  0,  3,  0,  6, 16],
       [ 3,  2,  3,  2,  1, 15,  0,  5,  7, 12],
       [ 7,  0, 10,  0,  2,  0, 19,  0,  5,  0],
       [ 0,  3,  3,  0,  0,  0,  0, 42,  0,  1],
       [ 1,  3,  6,  0,  0,  0,  0,  5, 20,  5],
       [ 2,  0,  2,  0,  0,  0,  0,  3,  3, 44]])

In [13]:
accuracies = cm_n.flatten() # accuracies for each combination
numbers    = cm.flatten()

In [14]:
n_classes = 10
y_true_lab = np.array([np.ones(n_classes)*i for i in range(0, n_classes)]).flatten()
y_pred_lab = np.array([np.arange(0, n_classes) for i in range(0, n_classes)]).flatten()

In [15]:
# Create a dictonary for images with the possible cases 
dictonary = {}
for yy, ll, ii in zip(test_labels, y_pred, test_images):
    try: 
        dictonary[hash((yy,ll))].append(ii)
    except:
        dictonary[hash((yy,ll))] = [ii]

In [16]:
# Sorting cases 
sorted_images = []
for i in range(n_classes):
    for j in range(n_classes):
        try:
            sorted_images.append(dictonary[hash((i,j))])
        except:
            sorted_images.append([np.zeros_like(ii)])

### ColumnDataSource 

In [17]:
data = {'y_true': y_true_lab, 'y_pred': y_pred_lab, 'acc': accuracies, 
        'imgs':sorted_images, 'num':numbers}
source = ColumnDataSource(data)

In [18]:
x_sq = np.arange(28)+0.5
y_sq = np.arange(28)+0.5
xx_sq, yy_sq = np.meshgrid(x_sq, y_sq)
xx_f = xx_sq.flatten()
yy_f = yy_sq.flatten()
image_source = ColumnDataSource(
                data=dict(
                    x = xx_f,
                    y = yy_f,
                    image=[]
                )
            )

### Defining color [palette](https://bokeh.pydata.org/en/latest/docs/reference/palettes.html)

In [19]:
from bokeh.palettes import viridis
mapper = LinearColorMapper(palette=viridis(10), low=0, high=1)

### Creating figure

In [20]:
TOOLS = "hover,save,pan,box_zoom,reset,wheel_zoom, tap"

In [21]:
p = figure(title="Confusion matrix MNIST",
           x_range=['0','1','2','3','4','5','6','7','8','9'], 
           y_range=['0','1','2','3','4','5','6','7','8','9'], 
           x_axis_location="above", plot_width=500, plot_height=400,
           tools=TOOLS, toolbar_location='below',
           tooltips=[('true', '@y_true'), ('pred', '@y_pred'), ('acc', '@acc'), ('#', '@num')])

In [22]:
p.grid.grid_line_color = None
p.axis.axis_line_color = None
p.axis.major_tick_line_color = None
p.axis.major_label_text_font_size = "5pt"
p.axis.major_label_standoff = 0
p.xaxis.major_label_orientation = 90

In [23]:
p.rect(x="y_pred", y="y_true", width=1, height=1,
       source=source,
       fill_color={'field': 'acc', 'transform': mapper},
       line_color=None)

callback = CustomJS(args=dict(s1=source, s2 = image_source), code= """       
        var a = cb_obj.indices;
        var data = s1.data;  // For CM 
        var data2 = s2.data; // For image plot
        
        var images = data['imgs'][a[0]];
        var random =  Math.floor(Math.random() * images.length);

        console.log(random)
        data2['image'] = images[random];
        s2.change.emit();
          """)
source.selected.js_on_change('indices', callback)

In [24]:
color_bar = ColorBar(color_mapper=mapper, major_label_text_font_size="7pt",
                     ticker=FixedTicker(ticks=np.linspace(0,1,10)),
                     label_standoff=6, border_line_color=None, location=(0, 0))
p.add_layout(color_bar, 'right')

In [25]:
f2 = figure(x_range=(0, 28), y_range=(0, 28), width=400, plot_height=400, title = 'Random Sample')
f2.square(x='x', y='y', fill_alpha= 'image', size=5, fill_color = "black", line_color = "black", source = image_source)

GlyphRenderer(id='1086', ...)

In [26]:
from bokeh.layouts import Row
show(Row(p,f2))

In [379]:
sorted_images[0][0].shape

(28, 28, 1)